In [2]:
import dash

ModuleNotFoundError: No module named 'dash'

In [1]:
import boto3
from io import TextIOWrapper
from gzip import GzipFile
import csv
import pandas as pd
import os
import geopandas as gpd
import awsS3CityflowTrips
import awsS3Connection
# Acceder a las variables de entorno
access_key = os.getenv('AWS_ACCES_KEY_ID')
secret_key = os.getenv('AWS_SECRET_ACCESS_KEY')

In [2]:
s3 = boto3.client('s3', aws_access_key_id=access_key,
        aws_secret_access_key=secret_key)

In [3]:
lista_de_opciones = awsS3CityflowTrips.getListRoutesFiles()


In [4]:
dataframe = awsS3Connection.get_data_given_index(lista_de_opciones[2])


---------------------------------
---------------------------------


In [5]:
# Convert latitude and longitude columns to numeric
dataframe['overlap_origin_lat'] = pd.to_numeric(dataframe['overlap_origin_lat'])
dataframe['overlap_origin_long'] = pd.to_numeric(dataframe['overlap_origin_long'])

# Create a GeoDataFrame
gdf = gpd.GeoDataFrame(
    dataframe, 
    geometry=gpd.points_from_xy(dataframe['overlap_origin_long'], dataframe['overlap_origin_lat'])
)

print(gdf.head())

     overlap_origin_long  overlap_origin_lat overlap_destination_long  \
13            -98.369071           20.080497               -98.382719   
26            -98.382890           20.096247               -98.374565   
63            -98.374736           20.090325               -98.353407   
72            -99.213560           20.478237               -99.211586   
126           -98.718789           20.061400               -98.722694   

    overlap_destination_lat trip_speed_mps travel_mode  \
13                20.096161           4.39     cycling   
26                20.073717            4.6     cycling   
63                20.106719           4.76     cycling   
72                20.474718           4.42     cycling   
126               20.054233           4.49     cycling   

                              trip_id                    geometry  
13   1c3314f0823b26916b03bff1ed6c655e   POINT (-98.36907 20.0805)  
26   40a5bfbf843eb5d794b54e66b8c9021e  POINT (-98.38289 20.09625)  
63   f2b

In [6]:
import folium

# Create a map centered around the mean latitude and longitude
m = folium.Map(location=[gdf['overlap_origin_lat'].mean(), gdf['overlap_origin_long'].mean()], zoom_start=12)

# Add points to the map
for idx, row in gdf.iterrows():
    folium.Marker([row['overlap_origin_lat'], row['overlap_origin_long']], popup=row['trip_id']).add_to(m)

# Display the map
m

In [11]:
# Read the shapefile
shapefile_path = 'path_to_your_shapefile.shp'
gdf_shapefile = gpd.read_file('geojson_hgo.geojson')
gdf_shapefile = gdf_shapefile.to_crs(epsg=4326)

# Create a folium map centered around the shapefile's centroid
m_shapefile = folium.Map(location=[gdf_shapefile.geometry.centroid.y.mean(), gdf_shapefile.geometry.centroid.x.mean()], zoom_start=12)

# Add the shapefile to the map
# Ensure the shapefile's geometry is set to EPSG:4326
folium.GeoJson(gdf_shapefile).add_to(m_shapefile)

# Display the map
m_shapefile

/tmp/ipykernel_3232/2667152484.py:7: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  m_shapefile = folium.Map(location=[gdf_shapefile.geometry.centroid.y.mean(), gdf_shapefile.geometry.centroid.x.mean()], zoom_start=12)


In [9]:
import dash
import dash_leaflet as dl
import dash_html_components as html
from dash.dependencies import Output, Input

# Initialize the Dash app
app = dash.Dash(__name__)

# Convert the GeoDataFrame to GeoJSON
geojson = gdf_shapefile.to_json()

# Define the layout of the app
app.layout = html.Div([
    dl.Map(center=[gdf_shapefile.geometry.centroid.y.mean(), gdf_shapefile.geometry.centroid.x.mean()], zoom=12, children=[
        dl.TileLayer(),
        dl.GeoJSON(data=geojson, id="geojson"),
    ], style={'width': '100%', 'height': '50vh', 'margin': "auto", "display": "block"}),
    html.Div(id='feature-info')
])

# Define the callback to handle click events
@app.callback(
    Output('feature-info', 'children'),
    [Input('geojson', 'click_feature')]
)
def display_feature_info(feature):
    if feature is not None:
        return html.Pre(str(feature['properties']))
    return "Click on a feature to see its properties"

# Run the app
if __name__ == '__main__':
    app.run_server(debug=True)

CVEGEO                NOMGEO  OID  \
0     01        Aguascalientes    1   
1     02       Baja California    2   
2     03   Baja California Sur    3   
3     04              Campeche    4   
4     05  Coahuila de Zaragoza    5   

                                            geometry  
0  POLYGON ((-102.28787 22.41649, -102.28753 22.4...  
1  MULTIPOLYGON (((-112.30067 28.38702, -112.2982...  
2  MULTIPOLYGON (((-109.89451 22.87476, -109.8946...  
3  MULTIPOLYGON (((-91.9565 20.197, -91.95636 20....  
4  POLYGON ((-102.31079 29.87695, -102.3105 29.87...